# Extractive text summarisation - test framework

First let's import all relevant modules

In [1]:
import sys
sys.path.append("/Users/frankkelly/Dropbox/Projects-new/sahaj_text_summarisation_clean/gradio-screen/")

import os
from pathlib import Path
import pandas as pd
import swifter

In [2]:

PROJECT_PATH = Path("./").absolute().parent
PROJECT_PATH

PosixPath('/Users/frankkelly/Dropbox/Projects-new/sahaj_text_summarisation_clean')

In [3]:
# %load_ext autoreload
# %autoreload 2
# %load_ext lab_black

In [4]:
iskaggle = os.environ.get("KAGGLE_KERNEL_RUN_TYPE", "")
if iskaggle:
    path = Path("../pariza/bbc-news-summary")
else:
    full_path = Path("pariza/bbc-news-summary")
    owner_slug = str(full_path).split("/")[0]
    dataset_slug = str(full_path).split("/")[1]
    print(owner_slug, dataset_slug)
    path = Path("../"+ dataset_slug)
    if not path.exists():
        import zipfile, kaggle

        kaggle.api.datasets_download(owner_slug=owner_slug, dataset_slug=dataset_slug)

pariza bbc-news-summary


In [5]:

from rouge import Rouge 

hypothesis = "the #### transcript is a written version of each day 's cnn student news program use this transcript to he    lp students with reading comprehension and vocabulary use the weekly newsquiz to test your knowledge of storie s you     saw on cnn student news"

reference = "this page includes the show transcript use the transcript to help students with reading comprehension and     vocabulary at the bottom of the page , comment for a chance to be mentioned on cnn student news . you must be a teac    her or a student age # # or older to request a mention on the cnn student news roll call . the weekly newsquiz tests     students ' knowledge of even ts in the news"

rouge = Rouge()
scores = rouge.get_scores(hypothesis, reference)

In [6]:
scores

[{'rouge-1': {'r': 0.42857142857142855,
   'p': 0.5833333333333334,
   'f': 0.49411764217577864},
  'rouge-2': {'r': 0.18571428571428572,
   'p': 0.3170731707317073,
   'f': 0.23423422957552154},
  'rouge-l': {'r': 0.3877551020408163,
   'p': 0.5277777777777778,
   'f': 0.44705881864636676}}]

In [7]:
# Load in the BBC news summaries - from datasets/bbc-news-summary/
data_path = Path(PROJECT_PATH, "bbc-news-summary/BBC News Summary")

data_path


PosixPath('/Users/frankkelly/Dropbox/Projects-new/sahaj_text_summarisation_clean/bbc-news-summary/BBC News Summary')

In [8]:
from dataclasses import dataclass, field
from typing import List

@dataclass()
class BBCNewsDataReader:
    base_folder: str
    exclusion: list = field(default_factory=list)
    
    @property
    def news_articles_folder(self):
        return self.base_folder / 'News Articles'
    
    @property
    def summaries_folder(self):
        return self.base_folder / 'Summaries'
    
    @property
    def categories(self):
        exclusion_folders = lambda x: x not in [".DS_Store"] + self.exclusion
        return filter(exclusion_folders, os.listdir(self.news_articles_folder))
    
    def to_df(self):
        df = pd.DataFrame(columns=['article', 'summary', 'category', 'filename'])
        for article_folder, summary_folder in self.__category_folders():
            category = article_folder.split('/')[-1]
            for filename in os.listdir(article_folder):
                if os.path.isfile(f'{article_folder}/{filename}'):
                    try:
                        article = self.__read_file(f'{article_folder}/{filename}')
                        summary = self.__read_file(f'{summary_folder}/{filename}')
                        # TODO: replace append with concat
                        df = df.append({'article': article, 'summary': summary, 'category': category, 'filename': filename}, ignore_index=True)
                    except UnicodeDecodeError:
                        pass
        return df
                
            
    def __category_folders(self):
        return [
            (f'{self.news_articles_folder}/{category}', f'{self.summaries_folder}/{category}') for category in self.categories
        ]
    
    
    def __read_file(self, filepath):
        with open(filepath) as file:
            return file.read()

In [9]:
data = BBCNewsDataReader(
        base_folder=data_path,
        # exclusion=['entertainment', 'tech', 'sport', 'politics'] # remove these to read all data
    ).to_df()

In [10]:
data.head()

article  \
0  Musicians to tackle US red tape\n\nMusicians' ...   
1  U2's desire to be number one\n\nU2, who have w...   
2  Rocker Doherty in on-stage fight\n\nRock singe...   
3  Snicket tops US box office chart\n\nThe film a...   
4  Ocean's Twelve raids box office\n\nOcean's Twe...   

                                             summary       category filename  
0  Nigel McCune from the Musicians' Union said Br...  entertainment  289.txt  
1  But they still want more.They have to want to ...  entertainment  262.txt  
2  Babyshambles, which he formed after his acrimo...  entertainment  276.txt  
3  A Series of Unfortunate Events also stars Scot...  entertainment  060.txt  
4  Ocean's Twelve, the crime caper sequel starrin...  entertainment  074.txt

In [19]:
# Load in the models

from src.text_rank_summarizer import summarize as summarize_extractive
from src.transformer_summarization import summarize_abstractive

# Get the summaries from the datasets and models

In [13]:
import time

def get_extractive_summary(article):
    try:
        start_time = time.time()
        summary = summarize_extractive(article)
        # print(f"Extractive summary took {time.time() - start_time} seconds")
        return (summary, time.time() - start_time)
    except Exception as e:
        print(e)
        return (None, None)


In [68]:
if not os.path.exists(PROJECT_PATH / "output"):

    data["extractive_summary"], data["extractive_time_taken"] = zip(*data["article"].swifter.apply(get_extractive_summary))

else:
    # find most recent output file
    output_files = [PROJECT_PATH / "output"/ f for f in os.listdir(PROJECT_PATH / "output") if f.endswith(".csv")]
    most_recent_file = max(output_files, key=os.path.getctime)
    data = pd.read_csv(PROJECT_PATH / "output" / most_recent_file)

data.head()


article  \
0  Musicians to tackle US red tape\n\nMusicians' ...   
1  U2's desire to be number one\n\nU2, who have w...   
2  Rocker Doherty in on-stage fight\n\nRock singe...   
3  Snicket tops US box office chart\n\nThe film a...   
4  Ocean's Twelve raids box office\n\nOcean's Twe...   

                                             summary       category filename  \
0  Nigel McCune from the Musicians' Union said Br...  entertainment  289.txt   
1  But they still want more.They have to want to ...  entertainment  262.txt   
2  Babyshambles, which he formed after his acrimo...  entertainment  276.txt   
3  A Series of Unfortunate Events also stars Scot...  entertainment  060.txt   
4  Ocean's Twelve, the crime caper sequel starrin...  entertainment  074.txt   

                                  extractive_summary  extractive_time_taken  \
0  Musicians to tackle US red tape\n\nMusicians' ...               0.180434   
1  The group were born when Mullen put an appeal ...               0.233310   
2  On Tuesday, Doherty and his three bandmates we...               0.091577   
3  Snicket tops US box office chart\n\nThe film a...               0.041918   
4  Soderbergh returns to direct the hit sequel wh...               0.066866   

                                 abstractive_summary  abstractive_time_taken  \
0  Musicians to tackle visa regulations blamed fo...                2.204936   
1  U2 have won three prestigious Grammy Awards fo...                3.837446   
2  Babyshambles played for 5,000 fans at Brixton ...                2.222508   
3  A Series of Unfortunate Events stars Jim Carre...                2.023628   
4  Ocean's Twelve takes $40.8m in weekend ticket ...                3.077000   

   extractive_rouge-l_f1  extractive_rouge-1_f1  ...  extractive_bleu-1_gram  \
0               0.630435               0.630435  ...                0.454079   
1               0.295652               0.301449  ...                0.087095   
2               0.544379               0.556213  ...                0.334225   
3               0.789916               0.789916  ...                0.666667   
4               0.678571               0.690476  ...                0.585999   

   extractive_bleu-2_gram  extractive_bleu-3_gram  extractive_bleu-4_gram  \
0                0.394064                0.380340                0.366328   
1                0.062160                0.055266                0.053216   
2                0.277850                0.262896                0.247574   
3                0.625000                0.594937                0.564103   
4                0.514034                0.495676                0.476939   

   abstractive_bleu-1_gram  abstractive_bleu-2_gram  abstractive_bleu-3_gram  \
0                 0.056204             1.746180e-02            2.664260e-309   
1                 0.001532             1.171177e-03             9.730036e-04   
2                 0.067459             3.334198e-02             1.951726e-02   
3                 0.287932             1.923615e-01             1.314470e-01   
4                 0.040769            2.591859e-309            2.591859e-309   

   abstractive_bleu-4_gram  extractive_sentence_bleu  \
0            2.664260e-309                  0.397361   
1             8.120157e-04                  0.063168   
2             1.000260e-02                  0.278827   
3             6.740872e-02                  0.611511   
4            2.591859e-309                  0.516580   

   abstractive_sentence_bleu  
0              9.135903e-156  
1               1.091183e-03  
2               2.574194e-02  
3               1.488396e-01  
4              1.632271e-232  

[5 rows x 24 columns]

In [88]:
data["article_length"] = data["article"].swifter.apply(len)

Pandas Apply: 100%|██████████| 2224/2224 [00:00<00:00, 394107.57it/s]


In [91]:
data["article_length"].describe()

count     2224.000000
mean      2264.986061
std       1364.376735
min        503.000000
25%       1447.750000
50%       1966.000000
75%       2804.250000
max      25485.000000
Name: article_length, dtype: float64

In [123]:
def print_summary_with_best_score(data, category, metric, summarisation_type, max_article_length=1500):
    if summarisation_type == "abstractive":
        other_summarisation_type = "extractive"
    else:
        other_summarisation_type = "abstractive"

    if max_article_length and (max_article_length > data.article_length.min()):
        data = data[data["article_length"] <= max_article_length]
    print(f"\n\n{summarisation_type} summary with best {metric} for {category}")
    article, score, summary, other_summary, human_summary = data[data['category'] == category].sort_values(by=f"{summarisation_type}_{metric}", ascending=False).iloc[0][["article", f"{summarisation_type}_{metric}", f"{summarisation_type}_summary", f"{other_summarisation_type}_summary", "summary"]]
    print(f"Summary by {summarisation_type}: \n{summary}")
    print(f"============{metric}: {score}=======")
    print(f"Summary by {other_summarisation_type} for comparison: \n{other_summary}")
    print("===========================================================")
    print(f"Human summary: \n{human_summary}")
    print("===========================================================")
    print(f"\nArticle: \n{article}")



In [127]:
print_summary_with_best_score(data, "business", "rouge-l_f1", "abstractive", max_article_length=None)



abstractive summary with best rouge-l_f1 for business
Summary by abstractive: 
Mitsubishi confirmed earlier reports of talks with PSA Peugeot Citroen.
But spokesman refused to comment on speculation that Mitsubishi could build cars for PSA.
Mitsibishi has been hit by a recall scandal and withdrawal of support from shareholder DaimlerChrysler.
============rouge-l_f1: 0.7010309231671804=======
Summary by extractive for comparison: 
Mitsubishi in Peugeot link talks

Trouble-hit Mitsubishi Motors is in talks with French carmaker PSA Peugeot Citroen about a possible alliance. 

On Tuesday Mitsubishi, the only major Japanese car firm in the red, confirmed earlier reports of negotiations. Mitsubishi's sales have slid 41% in the past year, catalysed by the revelation that the company had systematically been hiding records of faults and then secretly repairing vehicles. But a spokesman refused to comment on speculation that Mitsubishi could end up building cars for PSA and perhaps its Japanes

In [16]:
data[["extractive_summary", "extractive_time_taken"]].head()

extractive_summary  extractive_time_taken
0  Musicians to tackle US red tape\n\nMusicians' ...               0.180434
1  The group were born when Mullen put an appeal ...               0.233310
2  On Tuesday, Doherty and his three bandmates we...               0.091577
3  Snicket tops US box office chart\n\nThe film a...               0.041918
4  Soderbergh returns to direct the hit sequel wh...               0.066866

In [17]:
import datetime

if not os.path.exists(PROJECT_PATH / "output"):
    os.makedirs(PROJECT_PATH / "output")

def write_to_file(df):
    todays_date_and_time_string = str(datetime.datetime.now().strftime("%Y-%m-%d_%H-%M-%S"))
    filename = PROJECT_PATH / f"output/bbc_news_summaries_{todays_date_and_time_string}.csv"

    df.to_csv(filename, index=False)
    print(f"Wrote {filename}")

write_to_file(data)

Wrote /Users/frankkelly/Dropbox/Projects-new/sahaj_text_summarisation_clean/output/bbc_news_summaries_2022-06-27_09-11-18.csv


In [20]:
def get_abstractive_summary(article):
    try:
        start_time = time.time()
        summary = summarize_abstractive(article)
        return summary, time.time() - start_time
    except Exception as e:
        print(e)
        return None, None


In [21]:

data["abstractive_summary"], data["abstractive_time_taken"] = zip(*data["article"].swifter.apply(get_abstractive_summary))

Pandas Apply:   0%|          | 0/2224 [00:00<?, ?it/s]The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Pandas Apply:   0%|          | 2/2224 [00:02<42:11,  1.14s/it]The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Pandas Apply:   0%|          | 3/2224 [00:06<1:23:48,  2.26s/it]The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Pandas Apply:   0%|          | 4/2224 [00:08<1:23:12,  2.25s/it]The attention m

index out of range in self


Pandas Apply:  17%|█▋        | 385/2224 [17:02<1:03:29,  2.07s/it]The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Pandas Apply:  17%|█▋        | 386/2224 [17:05<1:04:41,  2.11s/it]The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Pandas Apply:  17%|█▋        | 387/2224 [17:07<1:09:48,  2.28s/it]The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Pandas Apply:  17%|█▋        | 388/2224 [17:10<1:12:34,  2.37

index out of range in self


Pandas Apply:  82%|████████▏ | 1824/2224 [1:53:44<26:01,  3.90s/it]The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Pandas Apply:  82%|████████▏ | 1825/2224 [1:53:47<25:50,  3.89s/it]The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Pandas Apply:  82%|████████▏ | 1826/2224 [1:53:50<23:34,  3.55s/it]The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Pandas Apply:  82%|████████▏ | 1827/2224 [1:53:54<24:35,  

In [22]:
write_to_file(data)

Wrote /Users/frankkelly/Dropbox/Projects-new/sahaj_text_summarisation_clean/output/bbc_news_summaries_2022-06-27_12-04-54.csv


In [59]:
data.article.describe()

count                                                  2224
unique                                                 2126
top       Rings of steel combat net attacks\n\nGambling ...
freq                                                      2
Name: article, dtype: object

In [60]:
data[["article", "summary"]].describe()

article  \
count                                                2224   
unique                                               2126   
top     Rings of steel combat net attacks\n\nGambling ...   
freq                                                    2   

                                                  summary  
count                                                2224  
unique                                               2080  
top     Christian Harris, partnership manager of mobil...  
freq                                                    2

In [25]:
data[["article", "summary"]].isna().sum()

article    0
summary    0
dtype: int64

In [63]:
data.head()

article  \
0  Musicians to tackle US red tape\n\nMusicians' ...   
1  U2's desire to be number one\n\nU2, who have w...   
2  Rocker Doherty in on-stage fight\n\nRock singe...   
3  Snicket tops US box office chart\n\nThe film a...   
4  Ocean's Twelve raids box office\n\nOcean's Twe...   

                                             summary       category filename  \
0  Nigel McCune from the Musicians' Union said Br...  entertainment  289.txt   
1  But they still want more.They have to want to ...  entertainment  262.txt   
2  Babyshambles, which he formed after his acrimo...  entertainment  276.txt   
3  A Series of Unfortunate Events also stars Scot...  entertainment  060.txt   
4  Ocean's Twelve, the crime caper sequel starrin...  entertainment  074.txt   

                                  extractive_summary  extractive_time_taken  
0  Musicians to tackle US red tape\n\nMusicians' ...               0.070512  
1  The group were born when Mullen put an appeal ...               0.130277  
2  On Tuesday, Doherty and his three bandmates we...               0.058528  
3  Snicket tops US box office chart\n\nThe film a...               0.032637  
4  Soderbergh returns to direct the hit sequel wh...               0.047105

In [31]:
def get_rouge_score(row, summarisation_type, rouge_type):
    try:
        return rouge.get_scores(row[f"{summarisation_type}_summary"], row["summary"])[0][rouge_type]["f"]
    except Exception as e:
        print(e)
        return None

In [32]:
for summarisation_type in ["extractive", "abstractive"]:
    print(f"{summarisation_type}")
    for rouge_type in ["rouge-l", "rouge-1", "rouge-2"]:
        print(f"\t{rouge_type}")
        data[f"{summarisation_type}_{rouge_type}_f1"] = data.swifter.apply(lambda row: get_rouge_score(row, summarisation_type, rouge_type), axis=1)

extractive
	rouge-l


Pandas Apply: 100%|██████████| 2224/2224 [00:19<00:00, 112.53it/s]


	rouge-1


Pandas Apply: 100%|██████████| 2224/2224 [00:19<00:00, 113.23it/s]


	rouge-2


...

Pandas Apply: 100%|██████████| 2224/2224 [00:09<00:00, 242.60it/s]


	rouge-2


Pandas Apply:  19%|█▉        | 430/2224 [00:01<00:06, 286.36it/s]

Pandas Apply:  84%|████████▎ | 1862/2224 [00:07<00:01, 198.72it/s]

Pandas Apply: 100%|██████████| 2224/2224 [00:09<00:00, 240.05it/s]


In [33]:
data.head()

article  \
0  Musicians to tackle US red tape\n\nMusicians' ...   
1  U2's desire to be number one\n\nU2, who have w...   
2  Rocker Doherty in on-stage fight\n\nRock singe...   
3  Snicket tops US box office chart\n\nThe film a...   
4  Ocean's Twelve raids box office\n\nOcean's Twe...   

                                             summary       category filename  \
0  Nigel McCune from the Musicians' Union said Br...  entertainment  289.txt   
1  But they still want more.They have to want to ...  entertainment  262.txt   
2  Babyshambles, which he formed after his acrimo...  entertainment  276.txt   
3  A Series of Unfortunate Events also stars Scot...  entertainment  060.txt   
4  Ocean's Twelve, the crime caper sequel starrin...  entertainment  074.txt   

                                  extractive_summary  extractive_time_taken  \
0  Musicians to tackle US red tape\n\nMusicians' ...               0.180434   
1  The group were born when Mullen put an appeal ...               0.233310   
2  On Tuesday, Doherty and his three bandmates we...               0.091577   
3  Snicket tops US box office chart\n\nThe film a...               0.041918   
4  Soderbergh returns to direct the hit sequel wh...               0.066866   

                                 abstractive_summary  abstractive_time_taken  \
0  Musicians to tackle visa regulations blamed fo...                2.204936   
1  U2 have won three prestigious Grammy Awards fo...                3.837446   
2  Babyshambles played for 5,000 fans at Brixton ...                2.222508   
3  A Series of Unfortunate Events stars Jim Carre...                2.023628   
4  Ocean's Twelve takes $40.8m in weekend ticket ...                3.077000   

   extractive_rouge-l_f1  extractive_rouge-1_f1  extractive_rouge-2_f1  \
0               0.630435               0.630435               0.558704   
1               0.295652               0.301449               0.217213   
2               0.544379               0.556213               0.452174   
3               0.789916               0.789916               0.743243   
4               0.678571               0.690476               0.611872   

   abstractive_rouge-l_f1  abstractive_rouge-1_f1  abstractive_rouge-2_f1  
0                0.229730                0.256757                0.079208  
1                0.230769                0.237762                0.146699  
2                0.374101                0.374101                0.180851  
3                0.525253                0.525253                0.339286  
4                0.187500                0.187500                0.024242

In [35]:
write_to_file(data)

Wrote /Users/frankkelly/Dropbox/Projects-new/sahaj_text_summarisation_clean/output/bbc_news_summaries_2022-06-27_12-16-18.csv


In [42]:
from nltk.translate.bleu_score import sentence_bleu, corpus_bleu


def calculate_sentence_bleu(reference: str, candidate: str):
    """Calculate the sentence BLEU score."""
    if candidate is not None:
        return sentence_bleu([reference.split()], candidate.split())
    else:
        return 0


def calculate_corpus_bleu(reference: str, candidate: str):
    """Calculate the corpus BLEU score."""
    if candidate is not None:
        try:
            return corpus_bleu([reference.split()], candidate.split())
        except Exception as e:
            print(e)
            return 0
    else:
        return 0


def calculate_n_gram_bleu(reference: str, candidate: str, n: int):
    """Calculate the n-gram BLEU score."""
    if candidate is not None:
        if n == 1:
            return sentence_bleu(
                [reference.split()], candidate.split(), weights=(1, 0, 0, 0)
            )
        elif n == 2:
            return sentence_bleu(
                [reference.split()], candidate.split(), weights=(0, 1, 0, 0)
            )
        elif n == 3:
            return sentence_bleu(
                [reference.split()], candidate.split(), weights=(0, 0, 1, 0)
            )
        elif n == 4:
            return sentence_bleu(
                [reference.split()], candidate.split(), weights=(0, 0, 0, 1)
            )
    else:
        return 0


In [36]:
for summarisation_type in ["extractive", "abstractive"]:
    for n in [1, 2, 3, 4]:
        data[f"{summarisation_type}_bleu-{n}_gram"] = data.swifter.apply(
            lambda row: calculate_n_gram_bleu(row.summary, row[f"{summarisation_type}_summary"], n), axis=1
        )


Pandas Apply:   4%|▍         | 100/2224 [00:00<00:02, 999.70it/s]/Users/frankkelly/Library/Caches/pypoetry/virtualenvs/abstractive-text-summarization-IMBEzmp5-py3.9/lib/python3.9/site-packages/nltk/translate/bleu_score.py:552: UserWarning: 
The hypothesis contains 0 counts of 2-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/Users/frankkelly/Library/Caches/pypoetry/virtualenvs/abstractive-text-summarization-IMBEzmp5-py3.9/lib/python3.9/site-packages/nltk/translate/bleu_score.py:552: UserWarning: 
The hypothesis contains 0 counts of 3-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/Users/frankkelly/Library/Caches/pypoetry/virtualenvs/abstractive-text-summarization-IMBE

In [37]:
for summarisation_type in ["extractive", "abstractive"]:
    data[f"{summarisation_type}_sentence_bleu"] = data.swifter.apply(
        lambda row: calculate_sentence_bleu(row.summary, row[f"{summarisation_type}_summary"]), axis=1
        )

Pandas Apply:   0%|          | 0/2224 [00:00<?, ?it/s]/Users/frankkelly/Library/Caches/pypoetry/virtualenvs/abstractive-text-summarization-IMBEzmp5-py3.9/lib/python3.9/site-packages/nltk/translate/bleu_score.py:552: UserWarning: 
The hypothesis contains 0 counts of 2-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/Users/frankkelly/Library/Caches/pypoetry/virtualenvs/abstractive-text-summarization-IMBEzmp5-py3.9/lib/python3.9/site-packages/nltk/translate/bleu_score.py:552: UserWarning: 
The hypothesis contains 0 counts of 3-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/Users/frankkelly/Library/Caches/pypoetry/virtualenvs/abstractive-text-summarization-IMBEzmp5-py3.9/

In [39]:
write_to_file(data)

Wrote /Users/frankkelly/Dropbox/Projects-new/sahaj_text_summarisation_clean/output/bbc_news_summaries_2022-06-27_18-09-38.csv


In [43]:
for summarisation_type in ["extractive", "abstractive"]:
    data[f"{summarisation_type}_corpus_bleu"] = data.swifter.apply(
        lambda row: calculate_corpus_bleu(row.summary, row[f"{summarisation_type}_summary"]), axis=1
        )

Pandas Apply:  55%|█████▌    | 1232/2224 [00:00<00:00, 6256.31it/s]

The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) 

Pandas Apply: 100%|██████████| 2224/2224 [00:00<00:00, 7783.49it/s]



The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 


Pandas Apply:   0%|          | 0/2224 [00:00<?, ?it/s]

The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) 

Pandas Apply:  45%|████▍     | 998/2224 [00:00<00:00, 7518.28it/s]

The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) 

Pandas Apply: 100%|██████████| 2224/2224 [00:00<00:00, 7379.46it/s]

The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) should be the same 
The number of hypotheses and their reference(s) 

Pandas Apply: 100%|██████████| 2224/2224 [00:00<00:00, 26749.17it/s]


In [73]:
data.head(2)

article  \
0  Musicians to tackle US red tape\n\nMusicians' ...   
1  U2's desire to be number one\n\nU2, who have w...   

                                             summary       category filename  \
0  Nigel McCune from the Musicians' Union said Br...  entertainment  289.txt   
1  But they still want more.They have to want to ...  entertainment  262.txt   

                                  extractive_summary  extractive_time_taken  \
0  Musicians to tackle US red tape\n\nMusicians' ...               0.180434   
1  The group were born when Mullen put an appeal ...               0.233310   

                                 abstractive_summary  abstractive_time_taken  \
0  Musicians to tackle visa regulations blamed fo...                2.204936   
1  U2 have won three prestigious Grammy Awards fo...                3.837446   

   extractive_rouge-l_f1  extractive_rouge-1_f1  ...  extractive_bleu-4_gram  \
0               0.630435               0.630435  ...                0.366328   
1               0.295652               0.301449  ...                0.053216   

   abstractive_bleu-1_gram  abstractive_bleu-2_gram  abstractive_bleu-3_gram  \
0                 0.056204                 0.017462            2.664260e-309   
1                 0.001532                 0.001171             9.730036e-04   

   abstractive_bleu-4_gram  extractive_sentence_bleu  \
0            2.664260e-309                  0.397361   
1             8.120157e-04                  0.063168   

   abstractive_sentence_bleu  extractive_corpus_bleu  abstractive_corpus_bleu  \
0              9.135903e-156                       0                        0   
1               1.091183e-03                       0                        0   

   article_length  
0            2260  
1            4810  

[2 rows x 27 columns]

In [166]:
def get_stats(df):
    stats = data[bleu_metric_columns + rouge_metric_columns].describe()
    return pd.DataFrame(stats).T



stats_df = get_stats(data)
stats_df

count      mean       std       min       25%  \
abstractive_bleu-1_gram    2224.0  0.098123  0.095781  0.000000  0.020695   
extractive_bleu-1_gram     2224.0  0.423002  0.186296  0.000000  0.282405   
abstractive_bleu-2_gram    2224.0  0.054610  0.064646  0.000000  0.008303   
extractive_bleu-2_gram     2224.0  0.357233  0.185437  0.000000  0.211375   
abstractive_bleu-3_gram    2224.0  0.038108  0.050619  0.000000  0.003806   
extractive_bleu-3_gram     2224.0  0.338315  0.180096  0.000000  0.196097   
abstractive_bleu-4_gram    2224.0  0.027900  0.041035  0.000000  0.001391   
extractive_bleu-4_gram     2224.0  0.324111  0.173555  0.000000  0.187960   
abstractive_sentence_bleu  2224.0  0.046177  0.058924  0.000000  0.003451   
extractive_sentence_bleu   2224.0  0.357533  0.181854  0.000000  0.215631   
abstractive_corpus_bleu    2224.0  0.000000  0.000000  0.000000  0.000000   
extractive_corpus_bleu     2224.0  0.000000  0.000000  0.000000  0.000000   
abstractive_rouge-l_f1     2222.0  0.321479  0.108022  0.082919  0.241291   
extractive_rouge-l_f1      2224.0  0.593915  0.156216  0.000000  0.490991   
abstractive_rouge-1_f1     2222.0  0.332316  0.107810  0.082919  0.252632   
extractive_rouge-1_f1      2224.0  0.601357  0.151665  0.000000  0.500000   
abstractive_rouge-2_f1     2222.0  0.168326  0.097887  0.000000  0.095890   
extractive_rouge-2_f1      2224.0  0.496029  0.179052  0.000000  0.373444   

                                50%       75%       max  
abstractive_bleu-1_gram    0.071599  0.144769  0.600000  
extractive_bleu-1_gram     0.425691  0.556173  0.936842  
abstractive_bleu-2_gram    0.030435  0.075952  0.454545  
extractive_bleu-2_gram     0.349805  0.487040  0.904255  
abstractive_bleu-3_gram    0.017705  0.051853  0.348837  
extractive_bleu-3_gram     0.330574  0.462399  0.870968  
abstractive_bleu-4_gram    0.010756  0.036802  0.327334  
extractive_bleu-4_gram     0.316347  0.445197  0.836957  
abstractive_sentence_bleu  0.023803  0.065779  0.414249  
extractive_sentence_bleu   0.352997  0.483154  0.886473  
abstractive_corpus_bleu    0.000000  0.000000  0.000000  
extractive_corpus_bleu     0.000000  0.000000  0.000000  
abstractive_rouge-l_f1     0.309278  0.391608  0.701031  
extractive_rouge-l_f1      0.593867  0.702461  1.000000  
abstractive_rouge-1_f1     0.320611  0.403361  0.722222  
extractive_rouge-1_f1      0.600000  0.705128  1.000000  
abstractive_rouge-2_f1     0.153846  0.224074  0.535211  
extractive_rouge-2_f1      0.497607  0.622222  0.982301

In [97]:
bleu_metric_columns = ["abstractive_bleu-1_gram", "extractive_bleu-1_gram", "abstractive_bleu-2_gram", "extractive_bleu-2_gram", "abstractive_bleu-3_gram", "extractive_bleu-3_gram", "abstractive_bleu-4_gram", "extractive_bleu-4_gram", "abstractive_sentence_bleu", "extractive_sentence_bleu", "abstractive_corpus_bleu", "extractive_corpus_bleu"]
rouge_metric_columns = ["abstractive_rouge-l_f1", "extractive_rouge-l_f1", "abstractive_rouge-1_f1", "extractive_rouge-1_f1", "abstractive_rouge-2_f1", "extractive_rouge-2_f1"]
id_columns = ["filename", "article_length", "category", "abstractive_time_taken", "extractive_time_taken"]
melted_data_df = data.melt(id_vars=id_columns, value_vars=bleu_metric_columns + rouge_metric_columns, var_name="metric", value_name="value")
melted_data_df.sample(5)

filename  article_length  category  abstractive_time_taken  \
7474   309.txt            1387  business                2.564245   
22966  437.txt            2745  business                5.601824   
38222  505.txt            1485  business                2.302880   
26339  338.txt            3854      tech                7.134902   
25121  394.txt            1007  business                3.725450   

       extractive_time_taken                   metric     value  
7474                0.045213   extractive_bleu-2_gram  0.476636  
22966               0.125792  abstractive_corpus_bleu  0.000000  
38222               0.053204    extractive_rouge-2_f1  0.391753  
26339               0.130673   extractive_corpus_bleu  0.000000  
25121               0.037687   extractive_corpus_bleu  0.000000

In [98]:
melted_data_df["summarisation_type"] = melted_data_df["metric"].swifter.apply(lambda x: x.split("_")[0])
melted_data_df["metric_type"] = melted_data_df["metric"].swifter.apply(lambda x: " ".join(x.split("_")[1:]))
melted_data_df.drop(columns=["metric"], inplace=True)
melted_data_df.head()

Pandas Apply: 100%|██████████| 40032/40032 [00:00<00:00, 841960.95it/s]


filename  article_length       category  abstractive_time_taken  \
0  289.txt            2260  entertainment                2.204936   
1  262.txt            4810  entertainment                3.837446   
2  276.txt            2126  entertainment                2.222508   
3  060.txt            1044  entertainment                2.023628   
4  074.txt            1581  entertainment                3.077000   

   extractive_time_taken     value summarisation_type  metric_type  
0               0.180434  0.056204        abstractive  bleu-1 gram  
1               0.233310  0.001532        abstractive  bleu-1 gram  
2               0.091577  0.067459        abstractive  bleu-1 gram  
3               0.041918  0.287932        abstractive  bleu-1 gram  
4               0.066866  0.040769        abstractive  bleu-1 gram

In [99]:
melted_data_df[melted_data_df.filename=="060.txt"].sample(5)

filename  article_length       category  abstractive_time_taken  \
25873  060.txt            2499       politics                4.662860   
3633   060.txt            2499       politics                4.662860   
20019  060.txt            1044  entertainment                2.023628   
32037  060.txt            2208          sport                3.014981   
23649  060.txt            2499       politics                4.662860   

       extractive_time_taken     value summarisation_type    metric_type  
25873               0.133565  0.000000         extractive    corpus bleu  
3633                0.133565  0.400607         extractive    bleu-1 gram  
20019               0.041918  0.611511         extractive  sentence bleu  
32037               0.077563  0.162500        abstractive     rouge-1 f1  
23649               0.133565  0.000000        abstractive    corpus bleu

In [100]:
melted_data_df["time_taken"] = melted_data_df[["summarisation_type", "abstractive_time_taken", "extractive_time_taken"]].apply(lambda x: x.abstractive_time_taken if x.summarisation_type == "abstractive" else x.extractive_time_taken, axis=1)
melted_data_df.drop(columns=["abstractive_time_taken", "extractive_time_taken"], inplace=True)
melted_data_df.sample(5)

filename  article_length       category     value summarisation_type  \
21795  325.txt            1787       politics  0.310662         extractive   
26106  381.txt            1056       politics  0.000000         extractive   
39047  423.txt            2312          sport  0.538745         extractive   
22453  168.txt            2000  entertainment  0.000000        abstractive   
22866  432.txt            1105       business  0.000000        abstractive   

         metric_type  time_taken  
21795  sentence bleu    0.060261  
26106    corpus bleu    0.039388  
39047     rouge-2 f1    0.089297  
22453    corpus bleu    2.361807  
22866    corpus bleu    5.470171

In [106]:
def reshape_with_metric_type_as_columns(df):
    df = df.pivot_table(index=["filename", "category", "summarisation_type", "time_taken", "article_length"], columns="metric_type", values="value")
    df.reset_index(inplace=True)
    return df

reshaped_df = reshape_with_metric_type_as_columns(melted_data_df)
reshaped_df.head()


metric_type filename       category summarisation_type  time_taken  \
0            001.txt       business        abstractive    2.929244   
1            001.txt       business         extractive    0.092893   
2            001.txt  entertainment        abstractive    2.360420   
3            001.txt  entertainment         extractive    0.049050   
4            001.txt       politics        abstractive    4.063093   

metric_type  article_length  bleu-1 gram  bleu-2 gram  bleu-3 gram  \
0                      2559     0.045183     0.026247     0.018690   
1                      2559     0.519581     0.389191     0.369819   
2                      1150     0.274861     0.158693     0.104659   
3                      1150     0.398173     0.361350     0.345023   
4                      2598     0.008673     0.003462     0.001524   

metric_type  bleu-4 gram  corpus bleu  rouge-1 f1  rouge-2 f1  rouge-l f1  \
0               0.012827          0.0    0.312057    0.180791    0.312057   
1               0.350119          0.0    0.623762    0.457364    0.613861   
2               0.067907          0.0    0.482759    0.262069    0.465517   
3               0.328215          0.0    0.575758    0.469136    0.560606   
4               0.000522          0.0    0.263158    0.072727    0.236842   

metric_type  sentence bleu  
0                 0.023091  
1                 0.402258  
2                 0.132690  
3                 0.357274  
4                 0.002211

In [137]:
import plotly.express as px
import re
w,h = 1000,800

def show_all(df, y, size):
    title = re.sub(r"_", " ", y)
    return px.scatter(
        df, x="time_taken", y=y, log_x=True, size=df[size], title=title, width=w, height=h, color="summarisation_type", labels={"time_taken": "Time taken (s)", "size": "Size of article (words)"}
        )
        
        # df, width=w, height=h, size=df[size]**2, title=title,
        # x='secs',  y='top1', log_x=True, color='family', hover_name='model', hover_data=[size])

In [151]:
figures_path =Path("../output/figures")
if not os.path.exists(figures_path):
    os.mkdir(figures_path)

print(f"saving to {os.path.abspath(figures_path)}")


saving to /Users/frankkelly/Dropbox/Projects-new/sahaj_text_summarisation_clean/output/figures


In [155]:
metric_columns = ["rouge-l f1", "rouge-1 f1", "rouge-2 f1", "bleu-1 gram", "bleu-2 gram", "bleu-3 gram", "bleu-4 gram", "sentence_bleu", "corpus_bleu"]
for metric in metric_columns:
    print(metric)
    fig = show_all(reshaped_df, metric, "article_length")
    fig.write_html(f"{figures_path}/{metric}.html")
    try:
        fig.write_image(f"{figures_path}/{metric}.png", engine="kaleido")
    except Exception as e:
        print(e)
        print("failed to save .png")
    fig.show()


rouge-l f1

Image export using the "kaleido" engine requires the kaleido package,
which can be installed using pip:
    $ pip install -U kaleido

failed to save .png


rouge-1 f1

Image export using the "kaleido" engine requires the kaleido package,
which can be installed using pip:
    $ pip install -U kaleido

failed to save .png


rouge-2 f1

Image export using the "kaleido" engine requires the kaleido package,
which can be installed using pip:
    $ pip install -U kaleido

failed to save .png


bleu-1 gram

Image export using the "kaleido" engine requires the kaleido package,
which can be installed using pip:
    $ pip install -U kaleido

failed to save .png


bleu-2 gram

Image export using the "kaleido" engine requires the kaleido package,
which can be installed using pip:
    $ pip install -U kaleido

failed to save .png


bleu-3 gram

Image export using the "kaleido" engine requires the kaleido package,
which can be installed using pip:
    $ pip install -U kaleido

failed to save .png


bleu-4 gram

Image export using the "kaleido" engine requires the kaleido package,
which can be installed using pip:
    $ pip install -U kaleido

failed to save .png


sentence_bleu


ValueError: Value of 'y' is not the name of a column in 'data_frame'. Expected one of ['filename', 'category', 'summarisation_type', 'time_taken', 'article_length', 'bleu-1 gram', 'bleu-2 gram', 'bleu-3 gram', 'bleu-4 gram', 'corpus bleu', 'rouge-1 f1', 'rouge-2 f1', 'rouge-l f1', 'sentence bleu'] but received: sentence_bleu

In [ ]:


for metric in bleu_metric_columns:
    fig = show_all(reshaped_df, metric, "article_length")
    fig.write_html(f"{figures_path}{metric}.html")
    fig.show()

In [119]:
show_all(reshaped_df, y="rouge-l f1", size="article_length")

In [122]:
show_all(reshaped_df, y="bleu-3 gram", size="article_length")